In [52]:
 
from datetime import datetime, timedelta
import json

from kafka import KafkaConsumer
import os
import json
import time
from collections import namedtuple
import heapq
import uuid
import pandas as pd
import s3fs
import pyarrow.parquet as pq


endpoint_url='https://storage.budsc.midwest-datascience.com'
s3 = s3fs.S3FileSystem(
    anon=True,
    client_kwargs={
        'endpoint_url': endpoint_url
    }
)


acceleration_columns = [
    'offset',
    'id',
    'ride_id',
    'uuid',
    'x',
    'y',
    'z',
#     't'
]
Acceleration = namedtuple('Acceleration', acceleration_columns)
def read_accelerations():
    df = pq.ParquetDataset(
        's3://data/processed/bdd/accelerations',
        filesystem=s3
    ).read_pandas().to_pandas()
    
    df = df[acceleration_columns].sort_values(by=['offset'])
    
    records = [Acceleration(*record) for record in df.to_records(index=False)]
    
    return records
accelerations = read_accelerations()


location_columns = [
    'offset',
    'id',
    'ride_id',
    'uuid',
    'course',
    'latitude',
    'longitude',
    'geohash',
    'speed',
    'accuracy',
     't'
]
Location = namedtuple('Location', location_columns)
def read_locations():
    df = pq.ParquetDataset(
        's3://data/processed/bdd/locations',
        filesystem=s3
    ).read_pandas().to_pandas()
    
    df = df[location_columns].sort_values(by=['offset'])
    
    records = [Location(*record) for record in df.to_records(index=False)]
    
    return records
    
locations = read_locations()





In [53]:
sdatetime= datetime.now()
stime= time.time()
interval = .1

In [57]:
accdict = {}
for offset, id, ride_id, uuid, x,y,z in accelerations:
    accdict.setdefault(offset, [],).append(dict(id=id, ride_id=ride_id, uuid=uuid, x=x, y=y, z=z))
    
for key, value in accdict.items():
    print(key, value)

0.8220608865228429 [{'id': '58682c5d48cad9d9e103431d773615bf', 'ride_id': 'c9a2b46c9aa515b632eddc45c4868482', 'uuid': '19b9aa10588646b3bf22c9b4865a7995', 'x': -0.994, 'y': 0.045, 'z': -0.036000000000000004}]
0.8420608865228429 [{'id': '58682c5d48cad9d9e103431d773615bf', 'ride_id': 'c9a2b46c9aa515b632eddc45c4868482', 'uuid': '19b9aa10588646b3bf22c9b4865a7995', 'x': -0.998, 'y': 0.046, 'z': -0.04}]
0.862060886522843 [{'id': '58682c5d48cad9d9e103431d773615bf', 'ride_id': 'c9a2b46c9aa515b632eddc45c4868482', 'uuid': '19b9aa10588646b3bf22c9b4865a7995', 'x': -0.999, 'y': 0.047, 'z': -0.036000000000000004}]
0.882060886522843 [{'id': '58682c5d48cad9d9e103431d773615bf', 'ride_id': 'c9a2b46c9aa515b632eddc45c4868482', 'uuid': '19b9aa10588646b3bf22c9b4865a7995', 'x': -0.999, 'y': 0.045, 'z': -0.034}]
0.9020608865228429 [{'id': '58682c5d48cad9d9e103431d773615bf', 'ride_id': 'c9a2b46c9aa515b632eddc45c4868482', 'uuid': '19b9aa10588646b3bf22c9b4865a7995', 'x': -0.999, 'y': 0.048, 'z': -0.033}]
0.922060

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [58]:
locatedict = {}
for offset, id, ride_id, uuid, course, latitude, longitude, geohash, speed, accuracy, t in locations:
    locatedict.setdefault(offset, [],).append(dict(id=id, ride_id=ride_id, uuid=uuid, course=course, latitude=latitude,
                                                  longitude=longitude, geohash=geohash, speed=speed, accuracy=accuracy,t=t))
for key, value in locatedict.items():
    print(key, value)


1.0779125295566454 [{'id': '85c61911b7fe2ced1000c33c9e932706', 'ride_id': '6760ffa3f41908695d1405b776c3e8d5', 'uuid': 'dad7eae44e784b549c8c5a3aa051a8c7', 'course': 158.203125, 'latitude': 40.677641336844, 'longitude': -73.81793000742218, 'geohash': 'dr5x2jpkmtcy', 'speed': 2.119999885559082, 'accuracy': 10.0, 't': '000.0'}]
1.525060886522843 [{'id': '58682c5d48cad9d9e103431d773615bf', 'ride_id': 'c9a2b46c9aa515b632eddc45c4868482', 'uuid': '19b9aa10588646b3bf22c9b4865a7995', 'course': 299.619140625, 'latitude': 40.76287002542555, 'longitude': -73.96194855681718, 'geohash': 'dr5ruuwscttz', 'speed': 0.0, 'accuracy': 10.0, 't': '000.0'}]
4.5250608865228426 [{'id': '58682c5d48cad9d9e103431d773615bf', 'ride_id': 'c9a2b46c9aa515b632eddc45c4868482', 'uuid': '19b9aa10588646b3bf22c9b4865a7995', 'course': 299.619140625, 'latitude': 40.76287038067684, 'longitude': -73.96194937863832, 'geohash': 'dr5ruuwsctv3', 'speed': 0.0, 'accuracy': 10.0, 't': '004.5'}]
5.077912529556645 [{'id': '85c61911b7fe2c

In [56]:
pretime=0
for foldtime in accdict.keys():
    print(foldtime)
    time.sleep(foldtime - pretime)
    print(foldtime)
    send_data('accelerations', accdict.get(foldtime), accelerations)
    pretime=foldtime

0.8220608865228429
0.8220608865228429
0.8420608865228429
0.8420608865228429
0.862060886522843
0.862060886522843
0.882060886522843
0.882060886522843
0.9020608865228429
0.9020608865228429
0.9220608865228429
0.9220608865228429
0.9420608865228429
0.9420608865228429
0.9630608865228429
0.9630608865228429
0.983060886522843
0.983060886522843
1.003060886522843
1.003060886522843
1.023060886522843
1.023060886522843
1.0239125295566454
1.0239125295566454
1.043060886522843
1.043060886522843
1.0439125295566454
1.0439125295566454
1.0629125295566453
1.0629125295566453
1.0630608865228428
1.0630608865228428
1.0829125295566453
1.0829125295566453
1.0830608865228428
1.0830608865228428
1.1019125295566454
1.1019125295566454
1.1030608865228428
1.1030608865228428
1.1219125295566454
1.1219125295566454
1.1230608865228429
1.1230608865228429
1.1409125295566453
1.1409125295566453
1.1430608865228429
1.1430608865228429
1.1609125295566454
1.1609125295566454
1.163060886522843
1.163060886522843
1.1809125295566454
1.18091

KeyboardInterrupt: 